# Production MCMC — All Population Synthesis Models

> **Source**: copied from `../pop_test_MCMC.ipynb`

This notebook runs the **structured jet MCMC** (7 parameters, $f_j \leq 10$) across
**all population synthesis samples** in a loop, with 32k–50k steps per population.

### Contents
1. Loop over all population synthesis models
2. MCMC sampling for each population
3. Cross-population plotting using `EpsilonModelPlotter`, `FjModelPlotter`, `LogNormalModelPlotter`
4. Jet angle distribution visualisation
5. Various diagnostic and comparison plots

> **Warning**: This is a computationally expensive notebook. Each population takes significant time.

In [1]:
%load_ext autoreload
%autoreload 2

from    src import init, posteriors, plots_oop 
import  emcee
import  numpy                   as np 
import  matplotlib.pyplot       as plt
from    math                    import inf
from    pathlib                 import Path
from    src.montecarlo          import log_likelihood, DEFAULT_LIMITS
from    src.prior_factory       import create_log_prior, log_prior, initialize_walkers
from    src.multiprocessing_MC  import run_mcmc_parallel 

plt.style.use('./configurations/style.mplstyle') #? Custom style, makes plots easier to read

In [2]:
population_folder = Path("datafiles") / "populations" / "samples"
#with glob find all the samples_*.dat files
samples = list(population_folder.glob('samples_*.dat'))
samp_names = [samp.name.split('samples_')[1].split('_BNSs')[0] for samp in samples]


base_dir    = "ProductionPop_fj10_20k_init_same/" #addded 2k was 10k before 

max_fj      = 10

custom_bounds = {
             'k'        : (1.5, 12),
             'L_L0'     : (-3, 2),
             'L_mu_E'   : (2.5, 4),
             'sigma_E'  : (0, 1),
             'L_mu_tau' : (-2, np.log10(2)), # put a maximum at 2 seconds as the real distribution is with a 2 second mean, this is shifted, so we really don't expect high values
             'sigma_tau': (0, 1.8),
             'f_j'      : (0, max_fj)
}
my_prior    = create_log_prior(custom_bounds)
nW 	        = 20

In [ ]:
total_num_samp  = len(samp_names)
max_n 			= 32_000
datafiles       = Path("datafiles")
default_params = None
for z_test in samp_names:
    print(f"Running for {z_test} ({samp_names.index(z_test)+1}/{total_num_samp})")
    # Where to find the datafiles and save the outputs
    extra_dir           = base_dir + z_test
    output_dir          = init.create_run_dir(extra_dir, use_timestamp = False)

    filename            = output_dir / "emcee.h5"
    backend             = emcee.backends.HDFBackend(filename)
        
    # GRB Jet structure assumptions
    params = {
        "alpha"         : -0.67,    # 2/3 from synchrotron
        "beta_s"        : -2.59,     # Average value from GRBs
        "n"             : 2,        # Smoothly broken power law curvature
        "theta_c"       : 3.4,      # Ghirlanda half-angle of jet core (from GW170817)
        "theta_v_max"   : 10,       # Maximum viewing angle of the jet (in degrees)
        "z_model"       : z_test    #? Optional, model to use for redshift distribution
    }

    default_params, default_interpolator, data_dict = init.initialize_simulation(datafiles, params) #? Catalogue data from fermi GBM

    def log_probability(thetas, default_params=default_params, default_interpolator=default_interpolator):
        # add a bit of noise to the parameters
        lp = my_prior(thetas)	
        
        if not np.isfinite(lp):
            return -inf, 0, 0, 0, 0, 0
        
        l_out = log_likelihood(thetas, params=default_params, interps=default_interpolator)
        
        if not np.isfinite(l_out[0]):
            return -inf, 0, 0, 0, 0, 0  

        return lp + l_out[0], l_out[1], l_out[2], l_out[3], l_out[4], l_out[5]
    
    initial     = np.array([2.5, 0.0, 3.6, 0.3, -0.5, 0.7, 0.9])
    ex_log_likelihood = log_probability(initial)[0]
    print(f"Example log likelihood: {ex_log_likelihood:.2f}")

    initial_     = np.array([2.5, 0.0, 3.6, 0.3, -0.5, 0.7, 5])
    ex_log_likelihood_ = log_probability(initial_)[0]
    print(f"Example log likelihood with fj > 2: {ex_log_likelihood_:.2f}")

    local_rate = default_params.local_rate
    pos         = initialize_walkers(nW) 
    if local_rate < 20:
        print("Low local rate, increasing number of steps to 40k")
        max_n = 50_000

    run_mcmc_parallel( 
        max_n       =   max_n,
        backend     =   backend,
        initial_pos =   pos,
        log_probability = log_probability,
        workers     =   None, #By default None occupies all your CPUs, manually change this if you don't want that
    )

Running for fiducial_delayed_A0.5 (1/64)
Loading existing directory  : Output_files/ProductionPop_fj10_20k_init_same/fiducial_delayed_A0.5
Using redshift model: samples_fiducial_delayed_A0.5_BNSs_0.dat with 60187 BNSs.
Generating temporal interpolators... (this may take a moment)
Preparing catalogue with limits: {'F_LIM': 4, 'T90_LIM': 2, 'EP_LIM_UPPER': 10000, 'EP_LIM_LOWER': 50}
Triggered events: 310, Trigger years: 16.66, Yearly rate: 18.61 events/year
Example log likelihood: -101.96
Example log likelihood with fj > 2: -604.90
Continuing from last run (40000/32000 iterations)
MCMC sampling already completed in previous runs.
Running for fiducial_delayed_A1.0 (2/64)
Loading existing directory  : Output_files/ProductionPop_fj10_20k_init_same/fiducial_delayed_A1.0
Using redshift model: samples_fiducial_delayed_A1.0_BNSs_0.dat with 342071 BNSs.
Generating temporal interpolators... (this may take a moment)
Preparing catalogue with limits: {'F_LIM': 4, 'T90_LIM': 2, 'EP_LIM_UPPER': 10000,

100%|██████████| 8972/8972 [56:49<00:00,  2.63it/s] 


Mean acceptance fraction: 0.051
MCMC sampling finished successfully.
Running for fiducial_HGoptimistic_A1.0 (10/64)
Loading existing directory  : Output_files/ProductionPop_fj10_20k_init_same/fiducial_HGoptimistic_A1.0
Using redshift model: samples_fiducial_HGoptimistic_A1.0_BNSs_0.dat with 57844 BNSs.
Generating temporal interpolators... (this may take a moment)
Preparing catalogue with limits: {'F_LIM': 4, 'T90_LIM': 2, 'EP_LIM_UPPER': 10000, 'EP_LIM_LOWER': 50}
Triggered events: 310, Trigger years: 16.66, Yearly rate: 18.61 events/year
Example log likelihood: -97.93
Example log likelihood with fj > 2: -653.62
Continuing from last run (40000/50000 iterations)


100%|██████████| 10000/10000 [13:14<00:00, 12.58it/s]


Mean acceptance fraction: 0.033
MCMC sampling finished successfully.
Running for fiducial_HGoptimistic_A3.0 (11/64)
Loading existing directory  : Output_files/ProductionPop_fj10_20k_init_same/fiducial_HGoptimistic_A3.0
Using redshift model: samples_fiducial_HGoptimistic_A3.0_BNSs_0.dat with 361335 BNSs.
Generating temporal interpolators... (this may take a moment)
Preparing catalogue with limits: {'F_LIM': 4, 'T90_LIM': 2, 'EP_LIM_UPPER': 10000, 'EP_LIM_LOWER': 50}
Triggered events: 310, Trigger years: 16.66, Yearly rate: 18.61 events/year
Example log likelihood: -585.10
Example log likelihood with fj > 2: -6256.97
Continuing from last run (40000/50000 iterations)


...

  0%|          | 0/10000 [00:00<?, ?it/s]/mnt/c/Users/Ludovico/Desktop/modules/emcee_de/src/emcee/moves/red_blue.py:99: RuntimeWarning: invalid value encountered in scalar subtract
  lnpdiff = f + nlp - state.log_prob[j]
100%|██████████| 10000/10000 [16:43<00:00,  9.96it/s]


Mean acceptance fraction: 0.048
MCMC sampling finished successfully.
Running for fiducial_klencki_A3.0 (31/64)
Loading existing directory  : Output_files/ProductionPop_fj10_20k_init_same/fiducial_klencki_A3.0
Using redshift model: samples_fiducial_klencki_A3.0_BNSs_0.dat with 213423 BNSs.
Generating temporal interpolators... (this may take a moment)
Preparing catalogue with limits: {'F_LIM': 4, 'T90_LIM': 2, 'EP_LIM_UPPER': 10000, 'EP_LIM_LOWER': 50}
Triggered events: 310, Trigger years: 16.66, Yearly rate: 18.61 events/year
Example log likelihood: -259.46
Example log likelihood with fj > 2: -3412.65
Continuing from last run (40000/50000 iterations)


100%|██████████| 10000/10000 [11:53<00:00, 14.03it/s]


Mean acceptance fraction: 0.027
MCMC sampling finished successfully.
Running for fiducial_klencki_A5.0 (32/64)
Loading existing directory  : Output_files/ProductionPop_fj10_20k_init_same/fiducial_klencki_A5.0
Using redshift model: samples_fiducial_klencki_A5.0_BNSs_0.dat with 299205 BNSs.
Generating temporal interpolators... (this may take a moment)
Preparing catalogue with limits: {'F_LIM': 4, 'T90_LIM': 2, 'EP_LIM_UPPER': 10000, 'EP_LIM_LOWER': 50}
Triggered events: 310, Trigger years: 16.66, Yearly rate: 18.61 events/year
Example log likelihood: -412.97
Example log likelihood with fj > 2: -4636.65
Continuing from last run (40000/50000 iterations)


 92%|█████████▏| 9156/10000 [10:00<00:55, 15.22it/s]

111.80374689542651